In [1]:
import pandas as pd
from imblearn.over_sampling import SMOTE
from sklearn.model_selection import train_test_split
from sklearn.ensemble import RandomForestClassifier
from sklearn.tree import DecisionTreeClassifier
from xgboost import XGBClassifier
from sklearn.metrics import roc_curve, auc
from sklearn.model_selection import GridSearchCV, train_test_split, cross_val_score




In [5]:
import pandas as pd
from imblearn.over_sampling import SMOTE
from sklearn.model_selection import GridSearchCV, cross_val_score
from xgboost import XGBClassifier

class ModelEvaluator:
    def __init__(self, algorithm, X_train, train_cols, target, X_test):
        self.algorithm = algorithm
        self.X_train = X_train
        self.train_cols = train_cols
        self.target = target
        self.X_test = X_test

    def evaluate(self):
        # Apply SMOTE to balance the dataset
        smote = SMOTE(random_state=42)
        X_train_resampled, y_train_resampled = smote.fit_resample(self.X_train[self.train_cols], self.X_train[self.target])

        model = XGBClassifier()

        # Define the parameter grid
        param_grid = {
            'n_estimators': [50, 100, 150],
            'max_depth': [3, 5, 7],
            'learning_rate': [0.1, 0.01, 0.001],
            'subsample': [0.6, 0.8, 1.0],
            'colsample_bytree': [0.6, 0.8, 1.0],
            'gamma': [0, 0.1, 0.2],
            'min_child_weight': [1, 3, 5]
        }

        # Parameter tuning using GridSearchCV
        grid_search = GridSearchCV(estimator=model, param_grid=param_grid, cv=5, scoring='roc_auc')
        grid_search.fit(X_train_resampled, y_train_resampled)

        # Best parameters and best score
        best_params = grid_search.best_params_
        best_score = grid_search.best_score_

        # Cross-validation
        cv_scores = cross_val_score(grid_search.best_estimator_, X_train_resampled, y_train_resampled, cv=5, scoring='roc_auc')

        # Final evaluation on test set
        y_pred = grid_search.predict_proba(self.X_test[self.train_cols])[:, 1]

        # Predict on test data
        self.X_test['Class_1_Probability'] = y_pred  

        return best_params, self.X_test


train_x = pd.read_csv('train_x_imputed.csv')
test_x = pd.read_csv('test_x_imputed.csv')

train_cols = list(train_x.columns)
train_cols.remove('Dependent_Variable')
test_cols = 'Dependent_Variable'  

# Instantiate ModelEvaluator with XGBoost
xgb_evaluator = ModelEvaluator('XGBoost', train_x, train_cols, test_cols, test_x)
xgb_best_params, test_predictions = xgb_evaluator.evaluate()

# Printing results
print("\nXGBoost:")
print("Best Parameters:", xgb_best_params)


/Users/rachitkumarsingh/Library/Python/3.9/lib/python/site-packages/xgboost/data.py:312: FutureWarning: is_sparse is deprecated and will be removed in a future version. Check `isinstance(dtype, pd.SparseDtype)` instead.
  if is_sparse(dtype):
/Users/rachitkumarsingh/Library/Python/3.9/lib/python/site-packages/xgboost/data.py:314: FutureWarning: is_categorical_dtype is deprecated and will be removed in a future version. Use isinstance(dtype, CategoricalDtype) instead
  elif is_categorical_dtype(dtype) and enable_categorical:
/Users/rachitkumarsingh/Library/Python/3.9/lib/python/site-packages/xgboost/data.py:345: FutureWarning: is_categorical_dtype is deprecated and will be removed in a future version. Use isinstance(dtype, CategoricalDtype) instead
  if is_categorical_dtype(dtype)
/Users/rachitkumarsingh/Library/Python/3.9/lib/python/site-packages/xgboost/data.py:336: FutureWarning: is_categorical_dtype is deprecated and will be removed in a future version. Use isinstance(dtype, Categor

KeyboardInterrupt: 